In [1]:
import os
import pyspark
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, from_json, greatest, lit, abs
from configparser import ConfigParser

In [2]:
jars_dir = "/home/dev/jars"
jars_list = [
    os.path.join(jars_dir, f) for f in os.listdir(jars_dir) if f.endswith(".jar")
]
jars_str = ",".join(jars_list)

In [3]:
# spark = (
#     SparkSession.builder.appName("LocalPySparkExample")
#     .config("spark.jars", jars_str)
#     .master("local[*]")
#     .config("spark.driver.memory", "60g")
#     .config("spark.driver.maxResultSize", "4g")
#     .config("spark.sql.shuffle.partitions", "400")
#     .config("spark.default.parallelism", "400")
#     .config("spark.executor.extraJavaOptions", "-XX:+UseG1GC -XX:InitiatingHeapOccupancyPercent=35")
#     .getOrCreate()
# )

# print('Spark Version: ', spark.version)

In [4]:
dataset_path = '/home/dev/dataset/kaggle-display-advertising-challenge-dataset'
dataset = ('readme.txt', 'train.txt', 'test.txt')
dataset_train_path = f"{dataset_path}/{dataset[1]}"
dataset_test_path = f"{dataset_path}/{dataset[2]}"

In [5]:
# data_train_df = spark.read.csv(dataset_train_path, header=False, sep='\t')
# data_train_df.describe().show()
# data_test_df = spark.read.csv(dataset_test_path, header=False, sep='\t')
# data_test_df.describe().show()

In [6]:
!pwd
!ls -l

/home/dev/workspace/machine-learning/playground/datascience/metaspore
total 112
drwxr-xr-x 2 dev users   4096 Jun 22 17:35 schema
-rw-r--r-- 1 dev users   1415 Jun 22 21:03 sparkmonitor_kernelextension.log
-rw-r--r-- 1 dev users 103049 Jun 22 21:02 tutorials.ipynb


In [7]:
import torch
import metaspore as ms

ROOT_DIR = '.'

class DemoModule(torch.nn.Module):
    def __init__(self):
        super().__init__()
        self._embedding_size = 16
        self._schema_dir = ROOT_DIR + '/schema/'
        self._column_name_path = self._schema_dir + 'column_name_demo.txt'
        self._combine_schema_path = self._schema_dir + 'combine_schema_demo.txt'
        self._sparse = ms.EmbeddingSumConcat(self._embedding_size, self._column_name_path, self._combine_schema_path)
        self._sparse.updater = ms.FTRLTensorUpdater()
        self._sparse.initializer = ms.NormalTensorInitializer(var=0.01)
        self._dense = torch.nn.Sequential(
            ms.nn.Normalization(self._sparse.feature_count * self._embedding_size),
            torch.nn.Linear(self._sparse.feature_count * self._embedding_size, 1024),
            torch.nn.ReLU(),
            torch.nn.Linear(1024, 512),
            torch.nn.ReLU(),
            torch.nn.Linear(512, 1),
        )

    def forward(self, x):
        x = self._sparse(x)
        x = self._dense(x)
        return torch.sigmoid(x)

In [8]:
module = DemoModule()

loaded combine schema from combine schema file './schema/combine_schema_demo.txt'
[2025-06-22 21:03:23.953] [info] [local_filesys.cpp:116] Opening local file ./schema/combine_schema_demo.txt with mode r
integer_feature_1
[2025-06-22 21:03:23.954] [info] add expr bkdr_hash(integer_feature_1, StringBKDRHashFunctionOption::name=integer_feature_1)
integer_feature_2
[2025-06-22 21:03:23.954] [info] add expr bkdr_hash(integer_feature_2, StringBKDRHashFunctionOption::name=integer_feature_2)
integer_feature_3
[2025-06-22 21:03:23.954] [info] add expr bkdr_hash(integer_feature_3, StringBKDRHashFunctionOption::name=integer_feature_3)
integer_feature_4
[2025-06-22 21:03:23.954] [info] add expr bkdr_hash(integer_feature_4, StringBKDRHashFunctionOption::name=integer_feature_4)
integer_feature_5
[2025-06-22 21:03:23.954] [info] add expr bkdr_hash(integer_feature_5, StringBKDRHashFunctionOption::name=integer_feature_5)
integer_feature_6
[2025-06-22 21:03:23.954] [info] add expr bkdr_hash(integer_feat

In [9]:
# import torch
# train_ds, val_ds = data_train_df.randomSplit(weights=[0.8, 0.2])

# print(train_ds.count(), val_ds.count())

In [10]:
model_out_path = ROOT_DIR + '/output/dev/model_out/'
estimator = ms.PyTorchEstimator(module=module,
                                worker_count=20,
                                server_count=5,
                                model_out_path=model_out_path,
                                experiment_name='0.1',
                                input_label_column_index=0)

In [11]:
column_names = []
with open(f'{ROOT_DIR}/schema/column_name_demo.txt', 'r') as f:
    for line in f:
        column_names.append(line.split(' ')[1].strip())
print(column_names)

spark_session = ms.spark.get_session(local=True,
                                     batch_size=100,
                                     worker_count=estimator.worker_count,
                                     server_count=estimator.server_count,
                                     log_level='INFO',
                                     spark_confs={'spark.eventLog.enabled':'false'})
train_dataset = ms.input.read_s3_csv(spark_session, dataset_train_path, delimiter='\t', column_names=column_names)

['label', 'integer_feature_1', 'integer_feature_2', 'integer_feature_3', 'integer_feature_4', 'integer_feature_5', 'integer_feature_6', 'integer_feature_7', 'integer_feature_8', 'integer_feature_9', 'integer_feature_10', 'integer_feature_11', 'integer_feature_12', 'integer_feature_13', 'categorical_feature_1', 'categorical_feature_2', 'categorical_feature_3', 'categorical_feature_4', 'categorical_feature_5', 'categorical_feature_6', 'categorical_feature_7', 'categorical_feature_8', 'categorical_feature_9', 'categorical_feature_10', 'categorical_feature_11', 'categorical_feature_12', 'categorical_feature_13', 'categorical_feature_14', 'categorical_feature_15', 'categorical_feature_16', 'categorical_feature_17', 'categorical_feature_18', 'categorical_feature_19', 'categorical_feature_20', 'categorical_feature_21', 'categorical_feature_22', 'categorical_feature_23', 'categorical_feature_24', 'categorical_feature_25', 'categorical_feature_26']


Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).


25/06/22 21:03:35 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
25/06/22 21:03:36 WARN Utils: Service 'SparkUI' could not bind on port 4040. Attempting port 4041.
25/06/22 21:03:37 INFO SharedState: Setting hive.metastore.warehouse.dir ('null') to the value of spark.sql.warehouse.dir.
25/06/22 21:03:37 INFO SharedState: Warehouse path is 'file:/home/dev/workspace/machine-learning/playground/datascience/metaspore/spark-warehouse'.
25/06/22 21:03:37 INFO InMemoryFileIndex: It took 46 ms to list leaf files for 1 paths.
ignore shuffle


In [ ]:
model = estimator.fit(train_dataset)

[2025-06-22 21:03:43.488] [info] PS job with coordinator address 172.50.0.2:34939 started.
[2025-06-22 21:03:43.488] [info] PSRunner::RunPS: pid: 7171, tid: 7441, thread: 0x7f48c47f8700
[2025-06-22 21:03:43.488] [info] PSRunner::RunPSCoordinator: pid: 7171, tid: 7441, thread: 0x7f48c47f8700
[2025-06-22 21:03:43.491] [info] ActorProcess::Receiving: Coordinator pid: 7171, tid: 7446, thread: 0x7f48baff5700
25/06/22 21:03:43 INFO SparkContext: Starting job: collect at /usr/local/lib/python3.8/dist-packages/metaspore/agent.py:291
25/06/22 21:03:43 INFO SparkContext: Starting job: collect at /usr/local/lib/python3.8/dist-packages/metaspore/agent.py:308
25/06/22 21:03:43 INFO DAGScheduler: Got job 0 (collect at /usr/local/lib/python3.8/dist-packages/metaspore/agent.py:291) with 5 output partitions
25/06/22 21:03:43 INFO DAGScheduler: Final stage: ResultStage 0 (collect at /usr/local/lib/python3.8/dist-packages/metaspore/agent.py:291)
25/06/22 21:03:43 INFO DAGScheduler: Parents of final stage

[2025-06-22 21:03:47.506] [info] PS job with coordinator address 172.50.0.2:34939 started.
[2025-06-22 21:03:47.506] [info] PSRunner::RunPS: pid: 7589, tid: 7631, thread: 0x7f158f949700
[2025-06-22 21:03:47.506] [info] PSRunner::RunPSWorker: pid: 7589, tid: 7631, thread: 0x7f158f949700
ps agent registered for process 7589 thread 0x7f15b93b9740
[2025-06-22 21:03:47.508] [info] ActorProcess::Receiving: Worker pid: 7589, tid: 7634, thread: 0x7f158e146700
[2025-06-22 21:03:47.627] [info] PS job with coordinator address 172.50.0.2:34939 started.
[2025-06-22 21:03:47.627] [info] PSRunner::RunPS: pid: 7493, tid: 7493, thread: 0x7f15b93b9740
[2025-06-22 21:03:47.627] [info] PSRunner::RunPSServer: pid: 7493, tid: 7493, thread: 0x7f15b93b9740
[2025-06-22 21:03:47.629] [info] ActorProcess::Receiving: Server pid: 7493, tid: 7637, thread: 0x7f158e947700
[2025-06-22 21:03:47.688] [info] PS job with coordinator address 172.50.0.2:34939 started.
[2025-06-22 21:03:47.688] [info] PSRunner::RunPS: pid: 7

[2025-06-22 21:03:48.324] [info] C[0]:9: The coordinator has connected to 5 servers and 20 workers.
PS Coordinator node C[0]:9 is ready.
25/06/22 21:03:48 INFO PythonRunner: Times: total = 3888, boot = 599, init = 2775, finish = 514
25/06/22 21:03:48 INFO PythonRunner: Times: total = 3889, boot = 556, init = 2934, finish = 399
25/06/22 21:03:48 INFO PythonRunner: Times: total = 3889, boot = 628, init = 2799, finish = 462
25/06/22 21:03:48 INFO PythonRunner: Times: total = 3889, boot = 624, init = 2827, finish = 438
25/06/22 21:03:48 INFO PythonRunner: Times: total = 3889, boot = 639, init = 2993, finish = 257
25/06/22 21:03:48 INFO PythonRunner: Times: total = 3889, boot = 670, init = 3111, finish = 108
25/06/22 21:03:48 INFO PythonRunner: Times: total = 3889, boot = 614, init = 3120, finish = 155
25/06/22 21:03:48 INFO PythonRunner: Times: total = 3889, boot = 603, init = 3136, finish = 150
25/06/22 21:03:48 INFO PythonRunner: Times: total = 3889, boot = 610, init = 3148, finish = 131

/usr/local/lib/python3.8/dist-packages/metaspore/estimator.py:116: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  module = torch.load(buf)
/usr/local/lib/python3.8/dist-packa

25/06/22 21:03:48 INFO SparkContext: Starting job: collect at PythonRDD.scala:180
25/06/22 21:03:48 INFO DAGScheduler: Got job 2 (collect at PythonRDD.scala:180) with 20 output partitions
25/06/22 21:03:48 INFO DAGScheduler: Final stage: ResultStage 2 (collect at PythonRDD.scala:180)
25/06/22 21:03:48 INFO DAGScheduler: Parents of final stage: List()
25/06/22 21:03:48 INFO DAGScheduler: Missing parents: List()
25/06/22 21:03:48 INFO DAGScheduler: Submitting ResultStage 2 (PythonRDD[5] at RDD at PythonRDD.scala:53), which has no missing parents
25/06/22 21:03:48 INFO MemoryStore: Block broadcast_3 stored as values in memory (estimated size 5.3 KiB, free 2.8 GiB)
25/06/22 21:03:48 INFO MemoryStore: Block broadcast_3_piece0 stored as bytes in memory (estimated size 3.3 KiB, free 2.8 GiB)
25/06/22 21:03:48 INFO BlockManagerInfo: Added broadcast_3_piece0 in memory on 172.50.0.2:36101 (size: 3.3 KiB, free: 2.8 GiB)
25/06/22 21:03:48 INFO SparkContext: Created broadcast 3 from broadcast at DA

...

2025-06-22 22:00:55.356 -- auc: 0.7893036399629987, Δauc: 0.7849236207015149, pcoc: 1.0005453650228022, Δpcoc: 0.9603580128062855, loss: 0.004572796077114441, Δloss: 0.004614643096923828, #instance: 22043957
25/06/22 22:00:55 INFO ArrowPythonRunner: Times: total = 1727217, boot = 119, init = 2, finish = 1727096
25/06/22 22:00:55 INFO DataWritingSparkTask: Writer for partition 34 is committing.
25/06/22 22:00:55 INFO DataWritingSparkTask: Committed partition 34 (task 299, attempt 0, stage 14.0)
25/06/22 22:00:55 INFO Executor: Finished task 34.0 in stage 14.0 (TID 299). 2062 bytes result sent to driver
25/06/22 22:00:55 INFO TaskSetManager: Starting task 47.0 in stage 14.0 (TID 312) (172.50.0.2, executor driver, partition 47, PROCESS_LOCAL, 4950 bytes) taskResourceAssignments Map()
25/06/22 22:00:55 INFO TaskSetManager: Finished task 34.0 in stage 14.0 (TID 299) in 1727264 ms on 172.50.0.2 (executor driver) (28/84)
25/06/22 22:00:55 INFO Executor: Running task 47.0 in stage 14.0 (TID 31

2025-06-22 22:00:55.914 -- auc: 0.7893033568177336, Δauc: 0.7827003283343686, pcoc: 1.0005445101657036, Δpcoc: 1.0285139892060877, loss: 0.004572789636969471, Δloss: 0.004464676856994629, #instance: 22045957
2025-06-22 22:00:56.054 -- auc: 0.7893045252299326, Δauc: 0.8176955504045087, pcoc: 1.0005495517184453, Δpcoc: 1.124183638054028, loss: 0.00457277149525741, Δloss: 0.004172820091247559, #instance: 22046957
2025-06-22 22:00:56.094 -- auc: 0.7893049898229012, Δauc: 0.7994027626398559, pcoc: 1.0005474976603077, Δpcoc: 0.9534769370907643, loss: 0.004572768720568053, Δloss: 0.004510410456603942, #instance: 22047938
2025-06-22 22:00:56.278 -- auc: 0.7893056561798769, Δauc: 0.8033430285308406, pcoc: 1.0005470377843955, Δpcoc: 0.9906945575699495, loss: 0.004572766727031745, Δloss: 0.004528813362121582, #instance: 22048938
2025-06-22 22:00:56.311 -- auc: 0.789306629490168, Δauc: 0.8102845225983124, pcoc: 1.000545550911382, Δpcoc: 0.9698644968856305, loss: 0.004572765106259047, Δloss: 0.0045

2025-06-22 22:00:56.974 -- auc: 0.7893090394938407, Δauc: 0.8017187655471822, pcoc: 1.000538705542195, Δpcoc: 0.9829989110449409, loss: 0.004572774485502626, Δloss: 0.0045245904922485355, #instance: 22053848
2025-06-22 22:00:57.064 -- auc: 0.7893089244963472, Δauc: 0.7873074967608613, pcoc: 1.0005412195103502, Δpcoc: 1.058886769401582, loss: 0.004572770198237696, Δloss: 0.004478219509124756, #instance: 22054848
2025-06-22 22:00:57.163 -- auc: 0.7893084135776645, Δauc: 0.7767228241800253, pcoc: 1.0005428640811858, Δpcoc: 1.03633628281174, loss: 0.004572777392371881, Δloss: 0.004731442928314209, #instance: 22055848


[2025-06-22 22:00:57.223] [error] Fail to extract sparse features for "_sparse". UNIMPLEMENTED: NotImplemented: Function 'bkdr_hash' has no kernel matching input types (array[null])

Stack trace returned 63 entries:
[bt] (0) /usr/local/lib/python3.8/dist-packages/metaspore/_metaspore.cpython-38-x86_64-linux-gnu.so(metaspore::SparseFeatureExtractor::extract(std::shared_ptr<arrow::RecordBatch>)+0x497) [0x7f15ab3f0bd7]
[bt] (1) /usr/local/lib/python3.8/dist-packages/metaspore/_metaspore.cpython-38-x86_64-linux-gnu.so(+0x50549e) [0x7f15ab45249e]
[bt] (2) /usr/local/lib/python3.8/dist-packages/metaspore/_metaspore.cpython-38-x86_64-linux-gnu.so(+0x44f6c9) [0x7f15ab39c6c9]
[bt] (3) /usr/bin/python3(PyCFunction_Call+0x59) [0x5f53d9]
[bt] (4) /usr/bin/python3(_PyObject_MakeTpCall+0x29e) [0x5f5fae]
[bt] (5) /usr/bin/python3() [0x50b0e3]
[bt] (6) /usr/bin/python3(_PyEval_EvalFrameDefault+0x5809) [0x56ff19]
[bt] (7) /usr/bin/python3() [0x50a88e]
[bt] (8) /usr/bin/python3(_PyEval_EvalFrameDefault+

25/06/22 22:00:57 ERROR Utils: Aborting task
org.apache.spark.api.python.PythonException: Traceback (most recent call last):
  File "/opt/spark/python/lib/pyspark.zip/pyspark/worker.py", line 686, in main
    process()
  File "/opt/spark/python/lib/pyspark.zip/pyspark/worker.py", line 678, in process
    serializer.dump_stream(out_iter, outfile)
  File "/opt/spark/python/lib/pyspark.zip/pyspark/sql/pandas/serializers.py", line 343, in dump_stream
    return ArrowStreamSerializer.dump_stream(self, init_stream_yield_batches(), stream)
  File "/opt/spark/python/lib/pyspark.zip/pyspark/sql/pandas/serializers.py", line 84, in dump_stream
    for batch in iterator:
  File "/opt/spark/python/lib/pyspark.zip/pyspark/sql/pandas/serializers.py", line 336, in init_stream_yield_batches
    for series in iterator:
  File "/opt/spark/python/lib/pyspark.zip/pyspark/worker.py", line 413, in func
    for result_batch, result_type in result_iter:
  File "/usr/local/lib/python3.8/dist-packages/metaspore/